In [3]:
import json
import plotly.express as px
import pandas as pd



In [4]:
from fractions import Fraction

def get_valid_weight(prompt):
    while True:
        try:
            input_str = input(prompt)
            # Check if input is a fraction
            if '/' in input_str:
                weight = float(Fraction(input_str))
            else:
                weight = float(input_str)
            
            # Validate the weight is within the correct range
            if not 0 <= weight <= 1:
                raise ValueError("Weight must be a number between 0 and 1")
            return weight
        except ValueError as e:
            print(e)

# Main loop for input validation and weight checks
while True:
    # Input validation for Low_income_weight
    Low_income_weight = get_valid_weight("Enter weight for Low income (between 0 and 1): ")

    # Input validation for Seniors_weight
    Seniors_weight = get_valid_weight("Enter weight for Seniors (between 0 and 1): ")

    # Input validation for Rent_weight
    Rent_weight = get_valid_weight("Enter weight for Rent (between 0 and 1): ")

    # Input validation for Public_transit_weight
    Public_transit_weight = get_valid_weight("Enter weight for Public transit (between 0 and 1): ")

    # Check if the sum of weights equals 1
    if abs(Low_income_weight + Seniors_weight + Rent_weight + Public_transit_weight - 1) < 1e-10:
        break
    else:
        print("Error: The sum of weights must be equal to 1. Please try again.")


In [5]:
# Load the Excel file into a DataFrame
excel_file = "Community Profiles Compiled.xlsx"  
df = pd.read_excel(excel_file)

In [6]:
Low_income = "Population in private households to whom low income concepts are applicable (Number in low income)"
Seniors ='Seniors'
rent ="Spend more than 30% on rent"
transit ="Public transit"


In [7]:
df['Low Income Index']=df[Low_income]*Low_income_weight
df['Seniors Index']=df['Seniors']*Seniors_weight
df['Rent Index']=df['Spend more than 30% on rent']*Rent_weight
df['Public Transit Index']=df['Public transit']*Public_transit_weight
df['Total Community Index']=df['Low Income Index']+df['Seniors Index']+df['Rent Index']+df['Public Transit Index']
max_total=df['Total Community Index'].max()
min_total=df['Total Community Index'].min()
df['Standardized Total Community Index']=(df['Total Community Index']-min_total)/(max_total-min_total)


Index=['Community Name','Low Income Index','Seniors Index','Rent Index','Public Transit Index','Total Community Index','Standardized Total Community Index']
df=df.filter(Index)
pd.set_option('display.max_rows',None)

df.to_csv('TotalDemandIndexStandardizedMethod2.csv',index=False)

In [8]:



   
    # Step 1: Load the CSV file
data = pd.read_csv('TotalDemandIndexStandardizedMethod2.csv')
    
    # Step 2: Sort the DataFrame
sorted_data = data.sort_values(by='Standardized Total Community Index', ascending=False)
    
    # Step 3: Extract Top 5 and Bottom 5
top_5_communities = sorted_data.head(5)
bottom_5_communities = sorted_data.tail(5)
    
    # Step 4: Display Results
print("Communities with the highest demand for transit:")
print(top_5_communities[['Community Name', 'Standardized Total Community Index']])
print("Communities with the lowest demand for transit:")
print(bottom_5_communities[['Community Name', 'Standardized Total Community Index']])


Communities with the highest demand for transit:
               Community Name  Standardized Total Community Index
14                   BELTLINE                            1.000000
56   DOWNTOWN COMMERCIAL CORE                            0.466289
185                   VARSITY                            0.446240
125            PANORAMA HILLS                            0.444146
86                  HILLHURST                            0.438987
Communities with the lowest demand for transit:
            Community Name  Standardized Total Community Index
106                MAYFAIR                            0.004909
59             EAGLE RIDGE                            0.004500
156  SCARBORO-SUNALTA WEST                            0.003682
13                 BELMONT                            0.002045
195            WOLF WILLOW                            0.000000


In [9]:


# Load Demand file and Geojson file and match communities coordinates with their standardized demand index
Demand_index_df = pd.read_csv('TotalDemandIndexStandardizedMethod2.csv')
with open('Census by Community 2019_20240401 copy.geojson', 'r') as file:
    geojson_data = json.load(file)

# Create the name mapping from the CSV data
name_mapping = {row['Community Name']: row['Standardized Total Community Index'] for index, row in Demand_index_df.iterrows()}

# Filter through the geojson file and organize the communities by their standardized demand
community_geojson = {
    "type": "FeatureCollection",
    "features": [f for f in geojson_data['features'] if f['properties']['name'] in name_mapping]
}

# Update feature properties with the standardized index
for feature in community_geojson['features']:
    feature['properties']['Standardized Index'] = name_mapping[feature['properties']['name']]

# Create a map that displays the demand index score for a community
fig = px.choropleth(community_geojson, 
                    geojson=community_geojson, 
                    locations=[f['properties']['name'] for f in community_geojson['features']],
                    featureidkey="properties.name",
                    color=[f['properties']['Standardized Index'] for f in community_geojson['features']],
                    projection="mercator",
                    color_continuous_scale="Viridis")  # Optional: Choose a color scale

# Update the layout with a title and color axis label
fig.update_layout(
    title_text='Demand Index',  # Set the title of the map
    geo=dict(
        showframe=False,  # Remove the frame around the map
        showcoastlines=False  # Remove coastlines (if not relevant)
    ),
    coloraxis_colorbar=dict(title='Standardized Demand Index')  # Set the title for the color scale
)

fig.update_geos(fitbounds="locations")
fig.show()
